In [1]:
import os
import sys
import time
from datetime import date
from datetime import datetime
import time
import json
import platform

import stoneburner
#//*** Custom Functions:
#//*** mr_clean_text(input_series)
#//*** tokenize_series(input_series)
#//*** remove_stop_words(input_series)

# //*** Imports and Load Data
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd

#//*** Use the whole window in the IPYNB editor
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))
subreddits = ["wallstreetbets", "stocks", "wallstreetbetsOGs", "spacs", "investing", "pennystocks", "stockmarket", "options", "robinhoodpennystocks", "wallstreetbetsnew", "smallstreetbets"]
filepath = "./data/"
filename_suffix = "_comments.csv.zip"
#//*** Maximize columns and rows displayed by pandas
pd.set_option('display.max_rows', 100)
pd.set_option('display.max_columns', None)

In [2]:
#//*** Input_filename: Comments to Process.
#//*** This will eventually be a list of files
#input_filename  =".\\data\\wallstreetbets_comments.csv.zip"

#//*** Path to processed files
output_filename = "./data/processed_reddit_v4_1min.csv.zip"

#//*** Path to the stock ticker JSON file
stock_ticker_filename = "./data/stock_tickers.json"

#//*** Convert Path to Mac formatting if needed
#if platform.system() == 'Darwin':
#    output_filename = output_filename.replace("\\","/")
#    stock_ticker_filename = stock_ticker_filename.replace("\\","/")

#//*** Load the Stock Tickers
f = open(stock_ticker_filename, "r")
symbols = json.loads(f.read())['symbols']

symbols = ["amc"]
f.close()

process_tfidf = False

print(symbols)
#//*** Convert symbols to lower case
symbols = [x.lower() for x in symbols]



raw_df = pd.DataFrame()

start_time = time.time()

#//*** Load each Subreddit for Aggregation
for subreddit in subreddits:
    #//*** Filepath + subreddit name + csv.zip
    input_filename = filepath+subreddit+filename_suffix

    #//*** Convert Path to Mac formatting if needed
    #if platform.system() == 'Darwin':
    #    input_filename = input_filename.replace("\\","/")
   
    print(f"Reading Compressed CSV: {input_filename}")
    
    #//*** Read Each DataFrame and combine with raw_df
    raw_df = pd.concat([raw_df,pd.read_csv(input_filename,compression='zip' )])

#//*** Reset the index, since multiple indexes have been combined
raw_df.reset_index(drop=True, inplace=True)

print(f"Files Loaded: {round(time.time()-start_time,2)}s")
print(f"Total Records: {len(raw_df)}")
    

['amc']
Reading Compressed CSV: ./data/wallstreetbets_comments.csv.zip
Reading Compressed CSV: ./data/stocks_comments.csv.zip
Reading Compressed CSV: ./data/wallstreetbetsOGs_comments.csv.zip
Reading Compressed CSV: ./data/spacs_comments.csv.zip
Reading Compressed CSV: ./data/investing_comments.csv.zip
Reading Compressed CSV: ./data/pennystocks_comments.csv.zip
Reading Compressed CSV: ./data/stockmarket_comments.csv.zip
Reading Compressed CSV: ./data/options_comments.csv.zip
Reading Compressed CSV: ./data/robinhoodpennystocks_comments.csv.zip
Reading Compressed CSV: ./data/wallstreetbetsnew_comments.csv.zip
Reading Compressed CSV: ./data/smallstreetbets_comments.csv.zip
Files Loaded: 53.22s
Total Records: 4432533


In [3]:
raw_df['body'] = raw_df['body'].astype('str')

#//*** Convert UTC to date (not datetime)
#//** Second pass goes from 12-21 to 4-19
try:
    raw_df['created_utc'] = raw_df['created_utc'].apply(lambda x: datetime.fromtimestamp(x))
except:
    print()
raw_df

score  total_awards_received         created_utc  is_submitter  \
0            2                    0.0 2012-04-11 09:46:43         False   
1            2                    0.0 2012-04-11 10:39:08         False   
2            1                    0.0 2012-04-11 11:02:31         False   
3            6                    0.0 2012-04-11 11:47:11         False   
4            1                    0.0 2012-04-11 12:44:33         False   
...        ...                    ...                 ...           ...   
4432528      1                    0.0 2021-06-30 18:34:33          True   
4432529      1                    0.0 2021-06-30 19:08:36         False   
4432530      0                    0.0 2021-06-30 20:11:10         False   
4432531      1                    0.0 2021-06-30 20:16:51         False   
4432532      2                    0.0 2021-06-30 20:40:35         False   

        author_fullname                                               body  \
0              t2_59t5b  This is a fantastic idea! I'll toss mine up in...   
1              t2_3zydq                                    INTC is on 4/17   
2              t2_5u44p  straddle, call, straddle, put, put, put, strad...   
3              t2_54yfv  GMCR falls, GOOG falls *slightly*, GRPN will g...   
4              t2_69krh  CROX 4/26\n\nBZH 5/1\n\ni'm expecting both to ...   
...                 ...                                                ...   
4432528     t2_8kmwyads  Jun 30, 9.30pm EST.\n\n  \nI just saw this pos...   
4432529     t2_ah5dhj6a  Good run through. The mill is running and we’r...   
4432530        t2_6ypqa                       Back to normal not there yet   
4432531     t2_9ypzayi0                                             💎👐🚀🚀🚀🚀   
4432532     t2_9t61te74                                  I'll accept that.   

              id    link_id   parent_id  stickied  \
0        c4b0pvu   t3_s4jw1    t3_s4jw1     False   
1        c4b1fpf   t3_s4jw1    t3_s4jw1     False   
2        c4b1rmm   t3_s4jw1    t3_s4jw1     False   
3        c4b2egm   t3_s4jw1    t3_s4jw1     False   
4        c4b389t   t3_s4jw1    t3_s4jw1     False   
...          ...        ...         ...       ...   
4432528  h3mqxmd  t3_ob3sgh   t3_ob3sgh     False   
4432529  h3mv22t  t3_nccfsi   t3_nccfsi     False   
4432530  h3n2dw6  t3_oaj3cj  t1_h3n2a0q     False   
4432531  h3n3265  t3_nwlrf9   t3_nwlrf9     False   
4432532  h3n5uwk  t3_oay1dx  t1_h3lv3vr     False   

                                                 permalink  retrieved_on  \
0                                                        0  1.428700e+09   
1                                                        0  1.428700e+09   
2                                                        0  1.428700e+09   
3                                                        0  1.428700e+09   
4                                                        0  1.428701e+09   
...                                                    ...           ...   
4432528  /r/smallstreetbets/comments/ob3sgh/crnt_cerago...  1.625356e+09   
4432529  /r/smallstreetbets/comments/nccfsi/possibly_th...  1.625358e+09   
4432530  /r/smallstreetbets/comments/oaj3cj/poww_blew_a...  1.625361e+09   
4432531  /r/smallstreetbets/comments/nwlrf9/sabr_dd_19_...  1.625362e+09   
4432532  /r/smallstreetbets/comments/oay1dx/core_one_la...  1.625363e+09   

               subreddit subreddit_id  \
0         wallstreetbets     t5_2th52   
1         wallstreetbets     t5_2th52   
2         wallstreetbets     t5_2th52   
3         wallstreetbets     t5_2th52   
4         wallstreetbets     t5_2th52   
...                  ...          ...   
4432528  smallstreetbets    t5_29phiw   
4432529  smallstreetbets    t5_29phiw   
4432530  smallstreetbets    t5_29phiw   
4432531  smallstreetbets    t5_29phiw   
4432532  smallstreetbets    t5_29phiw   

                                                      hash  
0        6827bc9e2385d87ecf7e53c54baab15186a20b47d0dde0...  
1     

In [39]:
for symbol in ['gme']:
    stock_df = pd.read_csv(f"./stocks/{symbol}_1min.csv.zip")
    
    #//trim the raw data set
    stock_df['time'] = pd.to_datetime(stock_df['time'])
    
    #//*** Remove Comments older than the first stock price
    tdf = raw_df[ raw_df['created_utc'] >= stock_df['time'].min() ]
    
    #stock_df = stock_df[stock_df['time'] <= raw_df['created_utc'].max() ]
    
    #stock_df = stock_df[stock_df['time'] >= raw_df['created_utc'].min() ]



                      time      open    high       low   close  volume
0      2021-07-12 20:00:00  189.5000  189.50  189.5000  189.50     417
1      2021-07-12 19:53:00  189.4400  189.44  189.4400  189.44     118
2      2021-07-12 19:22:00  189.0100  189.01  189.0100  189.01     102
3      2021-07-12 18:52:00  189.0000  189.00  189.0000  189.00     250
4      2021-07-12 17:53:00  189.5000  189.50  189.5000  189.50     163
...                    ...       ...     ...       ...     ...     ...
245622 2019-07-24 09:34:00    4.1200    4.13    4.1150    4.12    9663
245623 2019-07-24 09:33:00    4.1100    4.12    4.1100    4.12   10533
245624 2019-07-24 09:32:00    4.0948    4.11    4.0911    4.11    2378
245625 2019-07-24 09:31:00    4.0800    4.09    4.0500    4.09   47819
245626 2019-07-24 09:00:00    4.0900    4.09    4.0900    4.09     406

[245627 rows x 6 columns]


In [34]:
#stock_df = stock_df.sort_values("time")
stock_df

time      open    high       low   close  volume
0      2021-07-12 20:00:00  189.5000  189.50  189.5000  189.50     417
1      2021-07-12 19:53:00  189.4400  189.44  189.4400  189.44     118
2      2021-07-12 19:22:00  189.0100  189.01  189.0100  189.01     102
3      2021-07-12 18:52:00  189.0000  189.00  189.0000  189.00     250
4      2021-07-12 17:53:00  189.5000  189.50  189.5000  189.50     163
...                    ...       ...     ...       ...     ...     ...
245622 2019-07-24 09:34:00    4.1200    4.13    4.1150    4.12    9663
245623 2019-07-24 09:33:00    4.1100    4.12    4.1100    4.12   10533
245624 2019-07-24 09:32:00    4.0948    4.11    4.0911    4.11    2378
245625 2019-07-24 09:31:00    4.0800    4.09    4.0500    4.09   47819
245626 2019-07-24 09:00:00    4.0900    4.09    4.0900    4.09     406

[245627 rows x 6 columns]

In [19]:
tdf

score  total_awards_received         created_utc  is_submitter  \
10830        1                    0.0 2019-07-28 11:03:30          True   
10831        1                    0.0 2019-07-28 11:04:18          True   
10832        1                    0.0 2019-07-28 11:04:29          True   
10833        1                    0.0 2019-07-28 11:04:42          True   
10834        1                    0.0 2019-07-28 11:05:34          True   
...        ...                    ...                 ...           ...   
4432528      1                    0.0 2021-06-30 18:34:33          True   
4432529      1                    0.0 2021-06-30 19:08:36         False   
4432530      0                    0.0 2021-06-30 20:11:10         False   
4432531      1                    0.0 2021-06-30 20:16:51         False   
4432532      2                    0.0 2021-06-30 20:40:35         False   

        author_fullname                                               body  \
10830          t2_ezkey                                          Wtf is BM   
10831          t2_i32oq  BYND 11% swing break even for ATM contracts wt...   
10832         t2_1242ip  That's it, I'm just gonna buy RVLV shares and ...   
10833          t2_3xl90  No. Just Google it. Try something like "option...   
10834       t2_2mobn56i  I'm still on cycle for 10 more weeks bro and I...   
...                 ...                                                ...   
4432528     t2_8kmwyads  Jun 30, 9.30pm EST.\n\n  \nI just saw this pos...   
4432529     t2_ah5dhj6a  Good run through. The mill is running and we’r...   
4432530        t2_6ypqa                       Back to normal not there yet   
4432531     t2_9ypzayi0                                             💎👐🚀🚀🚀🚀   
4432532     t2_9t61te74                                  I'll accept that.   

              id    link_id   parent_id  stickied  \
10830    eva2865  t3_ciyob8   t3_ciyob8      True   
10831    eva2afi  t3_ci7p1h   t3_ci7p1h      True   
10832    eva2ayn  t3_ci7p1h   t3_ci7p1h      True   
10833    eva2bmd  t3_cinqli  t1_ev9ug7e      True   
10834    eva2e5i  t3_ci7p1h  t1_eva1ql2      True   
...          ...        ...         ...       ...   
4432528  h3mqxmd  t3_ob3sgh   t3_ob3sgh     False   
4432529  h3mv22t  t3_nccfsi   t3_nccfsi     False   
4432530  h3n2dw6  t3_oaj3cj  t1_h3n2a0q     False   
4432531  h3n3265  t3_nwlrf9   t3_nwlrf9     False   
4432532  h3n5uwk  t3_oay1dx  t1_h3lv3vr     False   

                                                 permalink  retrieved_on  \
10830    /r/wallstreetbets/comments/ciyob8/just_tried_b...  1.564337e+09   
10831    /r/wallstreetbets/comments/ci7p1h/weekend_disc...  1.564337e+09   
10832    /r/wallstreetbets/comments/ci7p1h/weekend_disc...  1.564337e+09   
10833    /r/wallstreetbets/comments/cinqli/goog_alphabe...  1.564337e+09   
10834    /r/wallstreetbets/comments/ci7p1h/weekend_disc...  1.564337e+09   
...                                                    ...           ...   
4432528  /r/smallstreetbets/comments/ob3sgh/crnt_cerago...  1.625356e+09   
4432529  /r/smallstreetbets/comments/nccfsi/possibly_th...  1.625358e+09   
4432530  /r/smallstreetbets/comments/oaj3cj/poww_blew_a...  1.625361e+09   
4432531  /r/smallstreetbets/comments/nwlrf9/sabr_dd_19_...  1.625362e+09   
4432532  /r/smallstreetbets/comments/oay1dx/core_one_la...  1.625363e+09   

               subreddit subreddit_id  \
10830     wallstreetbets     t5_2th52   
10831     wallstreetbets     t5_2th52   
10832     wallstreetbets     t5_2th52   
10833     wallstreetbets     t5_2th52   
10834     wallstreetbets     t5_2th52   
...                  ...          ...   
4432528  smallstreetbets    t5_29phiw   
4432529  smallstreetbets    t5_29phiw   
4432530  smallstreetbets    t5_29phiw   
4432531  smallstreetbets    t5_29phiw   
4432532  smallstreetbets    t5_29phiw   

                                                      hash  
10830    f9b6c613c1450a0a1fa8f570286954c98c481e73bbec13...  
10831 

In [41]:
comment_times = list(tdf['created_utc'])
stock_times = list(stock_df['time'].sort_values())



In [52]:
for x in stock_times:
    print(x)

2019-07-24 09:00:00
2019-07-24 09:31:00
2019-07-24 09:32:00
2019-07-24 09:33:00
2019-07-24 09:34:00
2019-07-24 09:35:00
2019-07-24 09:36:00
2019-07-24 09:37:00
2019-07-24 09:38:00
2019-07-24 09:39:00
2019-07-24 09:40:00
2019-07-24 09:41:00
2019-07-24 09:42:00
2019-07-24 09:43:00
2019-07-24 09:44:00
2019-07-24 09:45:00
2019-07-24 09:46:00
2019-07-24 09:47:00
2019-07-24 09:48:00
2019-07-24 09:49:00
2019-07-24 09:50:00
2019-07-24 09:51:00
2019-07-24 09:52:00
2019-07-24 09:53:00
2019-07-24 09:54:00
2019-07-24 09:55:00
2019-07-24 09:56:00
2019-07-24 09:57:00
2019-07-24 09:58:00
2019-07-24 09:59:00
2019-07-24 10:00:00
2019-07-24 10:01:00
2019-07-24 10:02:00
2019-07-24 10:03:00
2019-07-24 10:04:00
2019-07-24 10:05:00
2019-07-24 10:06:00
2019-07-24 10:07:00
2019-07-24 10:08:00
2019-07-24 10:09:00
2019-07-24 10:10:00
2019-07-24 10:11:00
2019-07-24 10:12:00
2019-07-24 10:13:00
2019-07-24 10:14:00
2019-07-24 10:15:00
2019-07-24 10:16:00
2019-07-24 10:17:00
2019-07-24 10:18:00
2019-07-24 10:19:00


2019-08-01 14:57:00
2019-08-01 14:58:00
2019-08-01 14:59:00
2019-08-01 15:00:00
2019-08-01 15:01:00
2019-08-01 15:02:00
2019-08-01 15:03:00
2019-08-01 15:04:00
2019-08-01 15:05:00
2019-08-01 15:06:00
2019-08-01 15:07:00
2019-08-01 15:08:00
2019-08-01 15:09:00
2019-08-01 15:10:00
2019-08-01 15:11:00
2019-08-01 15:12:00
2019-08-01 15:13:00
2019-08-01 15:14:00
2019-08-01 15:15:00
2019-08-01 15:16:00
2019-08-01 15:17:00
2019-08-01 15:18:00
2019-08-01 15:19:00
2019-08-01 15:20:00
2019-08-01 15:21:00
2019-08-01 15:22:00
2019-08-01 15:23:00
2019-08-01 15:24:00
2019-08-01 15:25:00
2019-08-01 15:26:00
2019-08-01 15:27:00
2019-08-01 15:28:00
2019-08-01 15:29:00
2019-08-01 15:30:00
2019-08-01 15:31:00
2019-08-01 15:32:00
2019-08-01 15:33:00
2019-08-01 15:34:00
2019-08-01 15:35:00
2019-08-01 15:36:00
2019-08-01 15:37:00
2019-08-01 15:38:00
2019-08-01 15:39:00
2019-08-01 15:40:00
2019-08-01 15:41:00
2019-08-01 15:42:00
2019-08-01 15:43:00
2019-08-01 15:44:00
2019-08-01 15:45:00
2019-08-01 15:46:00


2019-08-13 12:43:00
2019-08-13 12:44:00
2019-08-13 12:45:00
2019-08-13 12:46:00
2019-08-13 12:47:00
2019-08-13 12:48:00
2019-08-13 12:49:00
2019-08-13 12:50:00
2019-08-13 12:51:00
2019-08-13 12:52:00
2019-08-13 12:53:00
2019-08-13 12:54:00
2019-08-13 12:55:00
2019-08-13 12:56:00
2019-08-13 12:58:00
2019-08-13 12:59:00
2019-08-13 13:00:00
2019-08-13 13:01:00
2019-08-13 13:02:00
2019-08-13 13:03:00
2019-08-13 13:04:00
2019-08-13 13:05:00
2019-08-13 13:06:00
2019-08-13 13:07:00
2019-08-13 13:08:00
2019-08-13 13:09:00
2019-08-13 13:11:00
2019-08-13 13:12:00
2019-08-13 13:14:00
2019-08-13 13:15:00
2019-08-13 13:16:00
2019-08-13 13:17:00
2019-08-13 13:18:00
2019-08-13 13:19:00
2019-08-13 13:20:00
2019-08-13 13:21:00
2019-08-13 13:22:00
2019-08-13 13:23:00
2019-08-13 13:24:00
2019-08-13 13:25:00
2019-08-13 13:26:00
2019-08-13 13:27:00
2019-08-13 13:28:00
2019-08-13 13:29:00
2019-08-13 13:30:00
2019-08-13 13:31:00
2019-08-13 13:32:00
2019-08-13 13:33:00
2019-08-13 13:34:00
2019-08-13 13:35:00


2019-08-22 14:12:00
2019-08-22 14:13:00
2019-08-22 14:14:00
2019-08-22 14:15:00
2019-08-22 14:16:00
2019-08-22 14:17:00
2019-08-22 14:18:00
2019-08-22 14:19:00
2019-08-22 14:20:00
2019-08-22 14:21:00
2019-08-22 14:22:00
2019-08-22 14:23:00
2019-08-22 14:24:00
2019-08-22 14:25:00
2019-08-22 14:26:00
2019-08-22 14:27:00
2019-08-22 14:28:00
2019-08-22 14:29:00
2019-08-22 14:30:00
2019-08-22 14:31:00
2019-08-22 14:32:00
2019-08-22 14:33:00
2019-08-22 14:34:00
2019-08-22 14:35:00
2019-08-22 14:36:00
2019-08-22 14:37:00
2019-08-22 14:38:00
2019-08-22 14:39:00
2019-08-22 14:40:00
2019-08-22 14:41:00
2019-08-22 14:42:00
2019-08-22 14:43:00
2019-08-22 14:44:00
2019-08-22 14:45:00
2019-08-22 14:46:00
2019-08-22 14:47:00
2019-08-22 14:48:00
2019-08-22 14:49:00
2019-08-22 14:50:00
2019-08-22 14:51:00
2019-08-22 14:52:00
2019-08-22 14:53:00
2019-08-22 14:54:00
2019-08-22 14:55:00
2019-08-22 14:56:00
2019-08-22 14:57:00
2019-08-22 14:58:00
2019-08-22 14:59:00
2019-08-22 15:00:00
2019-08-22 15:01:00


2019-09-03 13:22:00
2019-09-03 13:23:00
2019-09-03 13:24:00
2019-09-03 13:25:00
2019-09-03 13:26:00
2019-09-03 13:27:00
2019-09-03 13:28:00
2019-09-03 13:29:00
2019-09-03 13:30:00
2019-09-03 13:31:00
2019-09-03 13:32:00
2019-09-03 13:33:00
2019-09-03 13:34:00
2019-09-03 13:35:00
2019-09-03 13:36:00
2019-09-03 13:37:00
2019-09-03 13:38:00
2019-09-03 13:39:00
2019-09-03 13:40:00
2019-09-03 13:41:00
2019-09-03 13:42:00
2019-09-03 13:43:00
2019-09-03 13:44:00
2019-09-03 13:45:00
2019-09-03 13:46:00
2019-09-03 13:47:00
2019-09-03 13:48:00
2019-09-03 13:49:00
2019-09-03 13:50:00
2019-09-03 13:51:00
2019-09-03 13:52:00
2019-09-03 13:53:00
2019-09-03 13:54:00
2019-09-03 13:55:00
2019-09-03 13:56:00
2019-09-03 13:57:00
2019-09-03 13:58:00
2019-09-03 13:59:00
2019-09-03 14:00:00
2019-09-03 14:01:00
2019-09-03 14:02:00
2019-09-03 14:03:00
2019-09-03 14:04:00
2019-09-03 14:05:00
2019-09-03 14:06:00
2019-09-03 14:07:00
2019-09-03 14:08:00
2019-09-03 14:09:00
2019-09-03 14:10:00
2019-09-03 14:11:00


...

2021-06-01 10:06:00
2021-06-01 10:07:00
2021-06-01 10:08:00
2021-06-01 10:09:00
2021-06-01 10:10:00
2021-06-01 10:11:00
2021-06-01 10:12:00
2021-06-01 10:13:00
2021-06-01 10:14:00
2021-06-01 10:15:00
2021-06-01 10:16:00
2021-06-01 10:17:00
2021-06-01 10:18:00
2021-06-01 10:19:00
2021-06-01 10:20:00
2021-06-01 10:21:00
2021-06-01 10:22:00
2021-06-01 10:23:00
2021-06-01 10:24:00
2021-06-01 10:25:00
2021-06-01 10:26:00
2021-06-01 10:27:00
2021-06-01 10:28:00
2021-06-01 10:29:00
2021-06-01 10:30:00
2021-06-01 10:31:00
2021-06-01 10:32:00
2021-06-01 10:33:00
2021-06-01 10:34:00
2021-06-01 10:35:00
2021-06-01 10:36:00
2021-06-01 10:37:00
2021-06-01 10:38:00
2021-06-01 10:39:00
2021-06-01 10:40:00
2021-06-01 10:41:00
2021-06-01 10:42:00
2021-06-01 10:43:00
2021-06-01 10:44:00
2021-06-01 10:45:00
2021-06-01 10:46:00
2021-06-01 10:47:00
2021-06-01 10:48:00
2021-06-01 10:49:00
2021-06-01 10:50:00
2021-06-01 10:51:00
2021-06-01 10:52:00
2021-06-01 10:53:00
2021-06-01 10:54:00
2021-06-01 10:55:00


2021-06-08 11:28:00
2021-06-08 11:29:00
2021-06-08 11:30:00
2021-06-08 11:31:00
2021-06-08 11:32:00
2021-06-08 11:33:00
2021-06-08 11:34:00
2021-06-08 11:35:00
2021-06-08 11:36:00
2021-06-08 11:37:00
2021-06-08 11:38:00
2021-06-08 11:39:00
2021-06-08 11:40:00
2021-06-08 11:41:00
2021-06-08 11:42:00
2021-06-08 11:43:00
2021-06-08 11:44:00
2021-06-08 11:45:00
2021-06-08 11:46:00
2021-06-08 11:47:00
2021-06-08 11:48:00
2021-06-08 11:49:00
2021-06-08 11:50:00
2021-06-08 11:51:00
2021-06-08 11:52:00
2021-06-08 11:53:00
2021-06-08 11:54:00
2021-06-08 11:55:00
2021-06-08 11:56:00
2021-06-08 11:57:00
2021-06-08 11:58:00
2021-06-08 11:59:00
2021-06-08 12:00:00
2021-06-08 12:01:00
2021-06-08 12:02:00
2021-06-08 12:03:00
2021-06-08 12:04:00
2021-06-08 12:05:00
2021-06-08 12:06:00
2021-06-08 12:07:00
2021-06-08 12:08:00
2021-06-08 12:09:00
2021-06-08 12:10:00
2021-06-08 12:11:00
2021-06-08 12:12:00
2021-06-08 12:13:00
2021-06-08 12:14:00
2021-06-08 12:15:00
2021-06-08 12:16:00
2021-06-08 12:17:00


2021-06-15 07:50:00
2021-06-15 07:52:00
2021-06-15 07:58:00
2021-06-15 08:01:00
2021-06-15 08:02:00
2021-06-15 08:03:00
2021-06-15 08:04:00
2021-06-15 08:05:00
2021-06-15 08:09:00
2021-06-15 08:12:00
2021-06-15 08:14:00
2021-06-15 08:17:00
2021-06-15 08:19:00
2021-06-15 08:23:00
2021-06-15 08:26:00
2021-06-15 08:28:00
2021-06-15 08:31:00
2021-06-15 08:37:00
2021-06-15 08:40:00
2021-06-15 08:41:00
2021-06-15 08:45:00
2021-06-15 08:46:00
2021-06-15 08:47:00
2021-06-15 08:48:00
2021-06-15 08:53:00
2021-06-15 08:55:00
2021-06-15 08:57:00
2021-06-15 08:59:00
2021-06-15 09:00:00
2021-06-15 09:01:00
2021-06-15 09:03:00
2021-06-15 09:04:00
2021-06-15 09:05:00
2021-06-15 09:06:00
2021-06-15 09:07:00
2021-06-15 09:08:00
2021-06-15 09:09:00
2021-06-15 09:11:00
2021-06-15 09:12:00
2021-06-15 09:13:00
2021-06-15 09:15:00
2021-06-15 09:16:00
2021-06-15 09:17:00
2021-06-15 09:18:00
2021-06-15 09:19:00
2021-06-15 09:23:00
2021-06-15 09:25:00
2021-06-15 09:26:00
2021-06-15 09:27:00
2021-06-15 09:28:00


2021-06-22 16:00:00
2021-06-22 16:01:00
2021-06-22 16:02:00
2021-06-22 16:03:00
2021-06-22 16:04:00
2021-06-22 16:05:00
2021-06-22 16:06:00
2021-06-22 16:07:00
2021-06-22 16:08:00
2021-06-22 16:11:00
2021-06-22 16:12:00
2021-06-22 16:13:00
2021-06-22 16:15:00
2021-06-22 16:16:00
2021-06-22 16:17:00
2021-06-22 16:20:00
2021-06-22 16:22:00
2021-06-22 16:24:00
2021-06-22 16:28:00
2021-06-22 16:29:00
2021-06-22 16:30:00
2021-06-22 16:32:00
2021-06-22 16:35:00
2021-06-22 16:39:00
2021-06-22 16:40:00
2021-06-22 16:41:00
2021-06-22 16:42:00
2021-06-22 16:44:00
2021-06-22 16:46:00
2021-06-22 16:47:00
2021-06-22 16:48:00
2021-06-22 16:49:00
2021-06-22 16:51:00
2021-06-22 16:52:00
2021-06-22 16:57:00
2021-06-22 16:59:00
2021-06-22 17:04:00
2021-06-22 17:05:00
2021-06-22 17:06:00
2021-06-22 17:07:00
2021-06-22 17:09:00
2021-06-22 17:10:00
2021-06-22 17:11:00
2021-06-22 17:13:00
2021-06-22 17:23:00
2021-06-22 17:26:00
2021-06-22 17:33:00
2021-06-22 17:35:00
2021-06-22 17:37:00
2021-06-22 17:41:00


2021-07-01 13:50:00
2021-07-01 13:51:00
2021-07-01 13:52:00
2021-07-01 13:53:00
2021-07-01 13:54:00
2021-07-01 13:55:00
2021-07-01 13:56:00
2021-07-01 13:57:00
2021-07-01 13:58:00
2021-07-01 13:59:00
2021-07-01 14:00:00
2021-07-01 14:01:00
2021-07-01 14:02:00
2021-07-01 14:03:00
2021-07-01 14:04:00
2021-07-01 14:05:00
2021-07-01 14:06:00
2021-07-01 14:07:00
2021-07-01 14:08:00
2021-07-01 14:09:00
2021-07-01 14:10:00
2021-07-01 14:11:00
2021-07-01 14:12:00
2021-07-01 14:13:00
2021-07-01 14:14:00
2021-07-01 14:15:00
2021-07-01 14:16:00
2021-07-01 14:17:00
2021-07-01 14:18:00
2021-07-01 14:19:00
2021-07-01 14:20:00
2021-07-01 14:21:00
2021-07-01 14:22:00
2021-07-01 14:23:00
2021-07-01 14:24:00
2021-07-01 14:25:00
2021-07-01 14:26:00
2021-07-01 14:27:00
2021-07-01 14:28:00
2021-07-01 14:29:00
2021-07-01 14:30:00
2021-07-01 14:31:00
2021-07-01 14:32:00
2021-07-01 14:33:00
2021-07-01 14:34:00
2021-07-01 14:35:00
2021-07-01 14:36:00
2021-07-01 14:37:00
2021-07-01 14:38:00
2021-07-01 14:39:00


In [56]:
def get_bin_time(needle,haystack):
    for index in range(len(haystack)):
        
        
        #if index > 100:
        #    return
        if (needle > haystack[index]) & (needle < haystack[index+1]): 
        #if needle > haystack[index]: 
            print(f"{len(haystack)}:{index} {haystack[index]} > {needle} < {haystack[index+1]}")
            
            return haystack[index]
        
#//*** Bin comments into times centered around pricing
bin_time = []

for x in comment_times:
    bin_time.append(get_bin_time(x,stock_times))
    #if len(bin_time) > 10000:
    #    break
print("Binned")
    


245627:1211 2019-07-26 19:59:00 > 2019-07-28 11:03:30 < 2019-07-29 04:51:00
245627:1211 2019-07-26 19:59:00 > 2019-07-28 11:04:18 < 2019-07-29 04:51:00
245627:1211 2019-07-26 19:59:00 > 2019-07-28 11:04:29 < 2019-07-29 04:51:00
245627:1211 2019-07-26 19:59:00 > 2019-07-28 11:04:42 < 2019-07-29 04:51:00
245627:1211 2019-07-26 19:59:00 > 2019-07-28 11:05:34 < 2019-07-29 04:51:00
245627:1211 2019-07-26 19:59:00 > 2019-07-28 11:05:41 < 2019-07-29 04:51:00
245627:1211 2019-07-26 19:59:00 > 2019-07-28 11:05:44 < 2019-07-29 04:51:00
245627:1211 2019-07-26 19:59:00 > 2019-07-28 11:05:52 < 2019-07-29 04:51:00
245627:1211 2019-07-26 19:59:00 > 2019-07-28 11:06:08 < 2019-07-29 04:51:00
245627:1211 2019-07-26 19:59:00 > 2019-07-28 11:06:25 < 2019-07-29 04:51:00
245627:1211 2019-07-26 19:59:00 > 2019-07-28 11:06:33 < 2019-07-29 04:51:00
245627:1211 2019-07-26 19:59:00 > 2019-07-28 11:06:44 < 2019-07-29 04:51:00
245627:1211 2019-07-26 19:59:00 > 2019-07-28 11:06:45 < 2019-07-29 04:51:00
245627:1211 

245627:2799 2019-08-01 19:53:00 > 2019-08-02 00:47:16 < 2019-08-02 08:01:00
245627:2799 2019-08-01 19:53:00 > 2019-08-02 00:47:17 < 2019-08-02 08:01:00
245627:2799 2019-08-01 19:53:00 > 2019-08-02 00:47:18 < 2019-08-02 08:01:00
245627:2799 2019-08-01 19:53:00 > 2019-08-02 00:47:20 < 2019-08-02 08:01:00
245627:2799 2019-08-01 19:53:00 > 2019-08-02 00:47:23 < 2019-08-02 08:01:00
245627:2799 2019-08-01 19:53:00 > 2019-08-02 00:47:26 < 2019-08-02 08:01:00
245627:2799 2019-08-01 19:53:00 > 2019-08-02 00:47:33 < 2019-08-02 08:01:00
245627:2799 2019-08-01 19:53:00 > 2019-08-02 00:47:36 < 2019-08-02 08:01:00
245627:2799 2019-08-01 19:53:00 > 2019-08-02 00:47:39 < 2019-08-02 08:01:00
245627:2799 2019-08-01 19:53:00 > 2019-08-02 00:47:43 < 2019-08-02 08:01:00
245627:2799 2019-08-01 19:53:00 > 2019-08-02 00:47:43 < 2019-08-02 08:01:00
245627:2799 2019-08-01 19:53:00 > 2019-08-02 00:48:27 < 2019-08-02 08:01:00
245627:2799 2019-08-01 19:53:00 > 2019-08-02 00:48:29 < 2019-08-02 08:01:00
245627:2799 

245627:2799 2019-08-01 19:53:00 > 2019-08-02 01:54:25 < 2019-08-02 08:01:00
245627:2799 2019-08-01 19:53:00 > 2019-08-02 01:54:25 < 2019-08-02 08:01:00
245627:2799 2019-08-01 19:53:00 > 2019-08-02 01:54:41 < 2019-08-02 08:01:00
245627:2799 2019-08-01 19:53:00 > 2019-08-02 01:54:55 < 2019-08-02 08:01:00
245627:2799 2019-08-01 19:53:00 > 2019-08-02 01:55:56 < 2019-08-02 08:01:00
245627:2799 2019-08-01 19:53:00 > 2019-08-02 01:55:57 < 2019-08-02 08:01:00
245627:2799 2019-08-01 19:53:00 > 2019-08-02 01:57:13 < 2019-08-02 08:01:00
245627:2799 2019-08-01 19:53:00 > 2019-08-02 01:57:29 < 2019-08-02 08:01:00
245627:2799 2019-08-01 19:53:00 > 2019-08-02 01:57:33 < 2019-08-02 08:01:00
245627:2799 2019-08-01 19:53:00 > 2019-08-02 01:57:55 < 2019-08-02 08:01:00
245627:2799 2019-08-01 19:53:00 > 2019-08-02 01:58:40 < 2019-08-02 08:01:00
245627:2799 2019-08-01 19:53:00 > 2019-08-02 01:58:52 < 2019-08-02 08:01:00
245627:2799 2019-08-01 19:53:00 > 2019-08-02 01:58:55 < 2019-08-02 08:01:00
245627:2799 

245627:13132 2019-09-06 18:00:00 > 2019-09-07 14:34:44 < 2019-09-09 07:01:00
245627:13132 2019-09-06 18:00:00 > 2019-09-07 14:35:05 < 2019-09-09 07:01:00
245627:13132 2019-09-06 18:00:00 > 2019-09-07 14:35:14 < 2019-09-09 07:01:00
245627:13132 2019-09-06 18:00:00 > 2019-09-07 14:35:19 < 2019-09-09 07:01:00
245627:13132 2019-09-06 18:00:00 > 2019-09-07 14:35:24 < 2019-09-09 07:01:00
245627:13132 2019-09-06 18:00:00 > 2019-09-07 14:36:38 < 2019-09-09 07:01:00
245627:13132 2019-09-06 18:00:00 > 2019-09-07 14:36:52 < 2019-09-09 07:01:00
245627:13132 2019-09-06 18:00:00 > 2019-09-07 14:37:26 < 2019-09-09 07:01:00
245627:13132 2019-09-06 18:00:00 > 2019-09-07 14:37:45 < 2019-09-09 07:01:00
245627:13132 2019-09-06 18:00:00 > 2019-09-07 14:37:53 < 2019-09-09 07:01:00
245627:13132 2019-09-06 18:00:00 > 2019-09-07 14:38:07 < 2019-09-09 07:01:00
245627:13132 2019-09-06 18:00:00 > 2019-09-07 14:38:08 < 2019-09-09 07:01:00
245627:13132 2019-09-06 18:00:00 > 2019-09-07 14:38:13 < 2019-09-09 07:01:00

245627:23643 2019-10-11 18:18:00 > 2019-10-14 02:35:26 < 2019-10-14 09:30:00
245627:23643 2019-10-11 18:18:00 > 2019-10-14 02:35:29 < 2019-10-14 09:30:00
245627:23643 2019-10-11 18:18:00 > 2019-10-14 02:35:48 < 2019-10-14 09:30:00
245627:23643 2019-10-11 18:18:00 > 2019-10-14 02:36:30 < 2019-10-14 09:30:00
245627:23643 2019-10-11 18:18:00 > 2019-10-14 02:37:14 < 2019-10-14 09:30:00
245627:23643 2019-10-11 18:18:00 > 2019-10-14 02:37:21 < 2019-10-14 09:30:00
245627:23643 2019-10-11 18:18:00 > 2019-10-14 02:37:39 < 2019-10-14 09:30:00
245627:23643 2019-10-11 18:18:00 > 2019-10-14 02:39:01 < 2019-10-14 09:30:00
245627:23643 2019-10-11 18:18:00 > 2019-10-14 02:39:23 < 2019-10-14 09:30:00
245627:23643 2019-10-11 18:18:00 > 2019-10-14 02:39:42 < 2019-10-14 09:30:00
245627:23643 2019-10-11 18:18:00 > 2019-10-14 02:40:25 < 2019-10-14 09:30:00
245627:23643 2019-10-11 18:18:00 > 2019-10-14 02:40:59 < 2019-10-14 09:30:00
245627:23643 2019-10-11 18:18:00 > 2019-10-14 02:41:04 < 2019-10-14 09:30:00

IndexError: list index out of range